# imports

In [1]:
!pip install transformers accelerate llama-index-llms-huggingface llama-index-embeddings-huggingface llama-index trulens_eval gradio -q

In [11]:
# Standard library imports
import os

# Third-party imports
import gradio as gr
import numpy as np
import openai as opai
opai.api_key = #upload your key
os.environ['OPENAI_API_KEY'] = #upload your key
from transformers import AutoModelForCausalLM

# Local module imports from llama_index
from llama_index.core import (
    ServiceContext,
    StorageContext,
    VectorStoreIndex,
    load_index_from_storage,
)
from llama_index.core import (
    Document,
    Settings,
    SimpleDirectoryReader,
    VectorStoreIndex,  # Duplicate, merged with above
)
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from llama_index.core.postprocessor import (SentenceTransformerRerank,MetadataReplacementPostProcessor)
from llama_index.llms.huggingface import HuggingFaceLLM
from llama_index.llms.openai import OpenAI as llama_openai
from llama_index.core.node_parser import (
    HierarchicalNodeParser,
    get_leaf_nodes,
    SentenceWindowNodeParser
)
from llama_index.core.query_engine import RetrieverQueryEngine
from llama_index.core.retrievers import AutoMergingRetriever

# Local module imports from trulens_eval
from trulens_eval import (
    Feedback,
    OpenAI as tr_opai,  # Duplicate, removed
    Tru,
    TruLlama,
)
from trulens_eval.feedback import Groundedness


# Normal query engine

In [3]:
documents = SimpleDirectoryReader(
    input_files=["/content/drive/MyDrive/DATA/Being_Citizens_in_Israel_1.pdf"]
).load_data()

In [ ]:
eval_questions = []
with open('/content/drive/MyDrive/DATA/Eval_questions.txt', 'r') as file:
    for line in file:
        # Remove newline character and convert to integer
        item = line.strip()
        print(item)
        eval_questions.append(item)

In [4]:
print(type(documents), "\n")
print(len(documents), "\n")
print(type(documents[0]))
print(documents[110])

<class 'list'> 

114 

<class 'llama_index.core.schema.Document'>
Doc ID: af3f9f02-7d3f-46fb-b1f7-33470eac0d64
Text: //  111) אוסר על מעביד להפלות בקבלה לעבודה         חלק ראשון
1959(תשי“טחוק שירות התעסוקה   חוק שוויון הזדמנויות או בפרסום דרישה
לקליטת עובדים מטעמי לאום או דת, ו ) אוסר על אפליה מטעמים של השתייכות
לאומית או 1988(תשמ“חבעבודה   דתית.  חלק משירותי הדת של הקבוצות השונות.
האגף לעדות   מדינת ישראל מממנת  ולהחזקתם של מוסדות דת, מסגדים וכנסיות.
המדינה גם מתקצ...


In [5]:
document = Document(text="\n\n".join([doc.text for doc in documents]))

In [6]:
Settings.embed_model = HuggingFaceEmbedding(
    model_name="aviadrom/HeArBERT"
)

Settings.llm = llama_openai(model="gpt-3.5-turbo", temperature=0,system_prompt="Always respond in Hebrew. Answer like a history teacher.")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


In [7]:
index = VectorStoreIndex.from_documents([document])

query_engine = index.as_query_engine()

In [9]:
tru = Tru()
tru.reset_database()

🦑 Tru initialized with db url sqlite:///default.sqlite .
🛑 Secret keys may be written to the database. See the `database_redact_keys` option of Tru` to prevent this.


In [12]:
openai = tr_opai()

qa_relevance = (
    Feedback(openai.relevance_with_cot_reasons, name="Answer Relevance")
    .on_input_output()
)

qs_relevance = (
    Feedback(openai.relevance_with_cot_reasons, name = "Context Relevance")
    .on_input()
    .on(TruLlama.select_source_nodes().node.text)
    .aggregate(np.mean)
)

grounded = Groundedness(groundedness_provider=openai)

groundedness = (
    Feedback(grounded.groundedness_measure_with_cot_reasons, name="Groundedness")
        .on(TruLlama.select_source_nodes().node.text)
        .on_output()
        .aggregate(grounded.grounded_statements_aggregator)
)

feedbacks = [qa_relevance, qs_relevance, groundedness]

✅ In Answer Relevance, input prompt will be set to __record__.main_input or `Select.RecordInput` .
✅ In Answer Relevance, input response will be set to __record__.main_output or `Select.RecordOutput` .
✅ In Context Relevance, input prompt will be set to __record__.main_input or `Select.RecordInput` .
✅ In Context Relevance, input response will be set to __record__.app.query.rets.source_nodes[:].node.text .


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


✅ In Groundedness, input source will be set to __record__.app.query.rets.source_nodes[:].node.text .
✅ In Groundedness, input statement will be set to __record__.main_output or `Select.RecordOutput` .


In [13]:
def get_prebuilt_trulens_recorder(query_engine, app_id):
    tru_recorder = TruLlama(
        query_engine,
        app_id=app_id,
        feedbacks=feedbacks
        )
    return tru_recorder

In [14]:
tru_recorder = get_prebuilt_trulens_recorder(query_engine,
                                             app_id="Direct Query Engine")

In [15]:
with tru_recorder as recording:
    for question in eval_questions:
        response = query_engine.query(question)

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

...

Groundedness per statement in source:   0%|          | 0/5 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

In [16]:
tru.get_leaderboard(app_ids=[])

Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

Context Relevance  Groundedness  Answer Relevance  \
app_id                                                                   
Direct Query Engine           0.302632      0.076667             0.985   

                     latency  total_cost  
app_id                                    
Direct Query Engine      6.0    0.003478

In [17]:
tru.run_dashboard()

Starting dashboard ...
npx: installed 22 in 3.17s

Go to this url and submit the ip given here. your url is: https://fine-dots-push.loca.lt

  Submit this IP Address: 34.125.9.233


<Popen: returncode: None args: ['streamlit', 'run', '--server.headless=True'...>

# auto-merging index

In [18]:
embed_model = HuggingFaceEmbedding(model_name="aviadrom/HeArBERT")

llm = llama_openai(model="gpt-3.5-turbo", temperature=0,system_prompt="Always respond in Hebrew. Answer like a history teacher.")

In [19]:
def build_automerging_index(
    documents,
    llm = llm,
    embed_model=embed_model,
    save_dir="merging_index",
    chunk_sizes=None,
):
    chunk_sizes = chunk_sizes or [2048, 512, 128]
    node_parser = HierarchicalNodeParser.from_defaults(chunk_sizes=chunk_sizes)
    nodes = node_parser.get_nodes_from_documents(documents)
    leaf_nodes = get_leaf_nodes(nodes)
    merging_context = ServiceContext.from_defaults(
        llm=llm,
        embed_model=embed_model,
    )
    storage_context = StorageContext.from_defaults()
    storage_context.docstore.add_documents(nodes)

    if not os.path.exists(save_dir):
        automerging_index = VectorStoreIndex(
            leaf_nodes, storage_context=storage_context, service_context=merging_context
        )
        automerging_index.storage_context.persist(persist_dir=save_dir)
    else:
        automerging_index = load_index_from_storage(
            StorageContext.from_defaults(persist_dir=save_dir),
            service_context=merging_context,
        )
    return automerging_index


def get_automerging_query_engine(
    automerging_index,
    similarity_top_k=12,
    rerank_top_n=6,
):
    base_retriever = automerging_index.as_retriever(similarity_top_k=similarity_top_k)
    retriever = AutoMergingRetriever(
        base_retriever, automerging_index.storage_context, verbose=True
    )
    rerank = SentenceTransformerRerank(
        top_n=rerank_top_n, model="BAAI/bge-reranker-base"
    )
    auto_merging_engine = RetrieverQueryEngine.from_args(
        retriever, node_postprocessors=[rerank]
    )
    return auto_merging_engine

In [20]:
def run_evals(eval_questions, tru_recorder, query_engine):
    for question in eval_questions:
        with tru_recorder as recording:
            response = query_engine.query(question)

In [21]:
auto_merging_index_0 = build_automerging_index(
    documents,
    llm=llm,
    embed_model=embed_model,
    save_dir="/content/drive/MyDrive/RAGindex/merging_index_2layerhe",
    chunk_sizes=[2048,512],
)

<ipython-input-19-84d6a02a8461>:12: DeprecationWarning: Call to deprecated class method from_defaults. (ServiceContext is deprecated, please use `llama_index.settings.Settings` instead.) -- Deprecated since version 0.10.0.
  merging_context = ServiceContext.from_defaults(


Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/5 [00:00<?, ?it/s]

In [22]:
auto_merging_engine_0 = get_automerging_query_engine(
    auto_merging_index_0,
    similarity_top_k=12,
    rerank_top_n=6,
)

config.json:   0%|          | 0.00/799 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.11G [00:00<?, ?B/s]

Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

tokenizer_config.json:   0%|          | 0.00/443 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

tokenizer.json:   0%|          | 0.00/17.1M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/279 [00:00<?, ?B/s]

In [23]:
tru_recorder = get_prebuilt_trulens_recorder(
    auto_merging_engine_0,
    app_id ='merging_index_2layer'
)

In [24]:
run_evals(eval_questions, tru_recorder, auto_merging_engine_0)

> Merging 1 nodes into parent node.
> Parent node id: 3ce3e540-27ee-462c-a9ee-434aa4a66655.
> Parent node text: שאלת חשיבה: 
"בדיון בטיוטת שרתוק, שנערך במינהלת 
 במאי, הציע בן-גוריון תיקון, 13העם ב 
והבהיר כי ...



Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

> Merging 1 nodes into parent node.
> Parent node id: 11584699-56a1-41cd-906b-e318d5ce4768.
> Parent node text: 16
 הכוונה לגוף הנבחר, הרשות המחוקקת 17
Á ראובן ריבלין, נשיא מדינת ישראל, מתייעץ
עם חברי “הרשימה ...

> Merging 1 nodes into parent node.
> Parent node id: addcf965-51a6-4832-8ef7-31cd40617a9e.
> Parent node text: אותם
בד בבד, מאחר שמדובר בהשקפה ליברלית, חלה לצד ההצדקה לזכות 
, שאינם משתייכים לתרבות הרוב, לרבו...



...

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

In [25]:
tru.get_leaderboard(app_ids=[])

Context Relevance  Groundedness  Answer Relevance  \
app_id                                                                    
merging_index_2layer           0.448485      0.571429          0.984211   
Direct Query Engine            0.302273      0.097727          0.977273   

                      latency  total_cost  
app_id                                     
merging_index_2layer      6.0    0.004402  
Direct Query Engine       6.0    0.003478

In [26]:
auto_merging_index_1 = build_automerging_index(
    documents,
    llm=llm,
    embed_model=embed_model,
    save_dir="/content/drive/MyDrive/RAGindex/merging_index_3layerhe",
    chunk_sizes=[2048,512,128],
)

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

<ipython-input-19-84d6a02a8461>:12: DeprecationWarning: Call to deprecated class method from_defaults. (ServiceContext is deprecated, please use `llama_index.settings.Settings` instead.) -- Deprecated since version 0.10.0.
  merging_context = ServiceContext.from_defaults(


Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

In [27]:
auto_merging_engine_1 = get_automerging_query_engine(
    auto_merging_index_1,
    similarity_top_k=12,
    rerank_top_n=6,
)

In [28]:
tru_recorder = get_prebuilt_trulens_recorder(
    auto_merging_engine_1,
    app_id ='merging_index_3layer'
)

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

In [29]:
run_evals(eval_questions, tru_recorder, auto_merging_engine_1)

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

...

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

In [30]:
tru.get_leaderboard(app_ids=[])

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Context Relevance  Groundedness  Answer Relevance  \
app_id                                                                    
merging_index_2layer           0.471212      0.455000          0.986364   
Direct Query Engine            0.302273      0.097727          0.977273   
merging_index_3layer                NaN           NaN          0.960000   

                      latency  total_cost  
app_id                                     
merging_index_2layer      6.0    0.004402  
Direct Query Engine       6.0    0.003478  
merging_index_3layer      6.0    0.001687

# sentace-window index

In [31]:
def build_sentence_window_index(
    documents,
    llm  = llm,
    embed_model=embed_model,
    sentence_window_size=3,
    save_dir="sentence_index",
):
    # create the sentence window node parser w/ default settings
    node_parser = SentenceWindowNodeParser.from_defaults(
        window_size=sentence_window_size,
        window_metadata_key="window",
        original_text_metadata_key="original_text",
    )
    sentence_context = ServiceContext.from_defaults(
        llm=llm,
        embed_model=embed_model,
        node_parser=node_parser,
    )
    if not os.path.exists(save_dir):
        sentence_index = VectorStoreIndex.from_documents(
            documents, service_context=sentence_context
        )
        sentence_index.storage_context.persist(persist_dir=save_dir)
    else:
        sentence_index = load_index_from_storage(
            StorageContext.from_defaults(persist_dir=save_dir),
            service_context=sentence_context,
        )

    return sentence_index


def get_sentence_window_query_engine(
    sentence_index, similarity_top_k=6, rerank_top_n=2
):
    # define postprocessors
    postproc = MetadataReplacementPostProcessor(target_metadata_key="window")
    rerank = SentenceTransformerRerank(
        top_n=rerank_top_n, model="BAAI/bge-reranker-base"
    )

    sentence_window_engine = sentence_index.as_query_engine(
        similarity_top_k=similarity_top_k, node_postprocessors=[postproc, rerank]
    )
    return sentence_window_engine

In [32]:
sentence_index_1 = build_sentence_window_index(
    documents,
    llm=llm,
    embed_model=embed_model,
    sentence_window_size=1,
    save_dir="/content/drive/MyDrive/RAGindex/sentence_index_1he"
)

<ipython-input-31-4b91ee8e6d63>:14: DeprecationWarning: Call to deprecated class method from_defaults. (ServiceContext is deprecated, please use `llama_index.settings.Settings` instead.) -- Deprecated since version 0.10.0.
  sentence_context = ServiceContext.from_defaults(


Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

In [33]:
sentence_window_engine_1 = get_sentence_window_query_engine(
    sentence_index_1
)

In [34]:
tru_recorder_1 = get_prebuilt_trulens_recorder(
    sentence_window_engine_1,
    app_id='sentence window engine 1'
)

In [35]:
run_evals(eval_questions, tru_recorder_1, sentence_window_engine_1)

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

...

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

In [36]:
tru.get_leaderboard(app_ids=[])

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

Context Relevance  Groundedness  Answer Relevance  \
app_id                                                                        
merging_index_2layer               0.471212      0.467857          0.986364   
sentence window engine 1           0.400000      0.000000          0.990909   
merging_index_3layer               0.340000           NaN          0.963636   
Direct Query Engine                0.302273      0.097727          0.977273   

                          latency  total_cost  
app_id                                         
merging_index_2layer          6.0    0.004402  
sentence window engine 1      6.0    0.001837  
merging_index_3layer          6.0    0.001687  
Direct Query Engine           6.0    0.003478

In [37]:
sentence_index_3 = build_sentence_window_index(
    documents,
    llm=llm,
    embed_model=embed_model,
    sentence_window_size=3,
    save_dir="/content/drive/MyDrive/RAGindex/sentence_index_3he"
)

<ipython-input-31-4b91ee8e6d63>:14: DeprecationWarning: Call to deprecated class method from_defaults. (ServiceContext is deprecated, please use `llama_index.settings.Settings` instead.) -- Deprecated since version 0.10.0.
  sentence_context = ServiceContext.from_defaults(


Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

In [38]:
sentence_window_engine_3 = get_sentence_window_query_engine(
    sentence_index_3
)

tru_recorder_3 = get_prebuilt_trulens_recorder(
    sentence_window_engine_3,
    app_id='sentence window engine 3'
)

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

In [43]:
run_evals(eval_questions, tru_recorder_3, sentence_window_engine_3)

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/1 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

...

Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/3 [00:00<?, ?it/s]

Groundedness per statement in source:   0%|          | 0/2 [00:00<?, ?it/s]

In [51]:
tru.get_leaderboard(app_ids=[])

Context Relevance  Groundedness  Answer Relevance  \
app_id                                                                        
sentence window engine 1           0.529545      0.534848          0.972727   
sentence window engine 3           0.514773      0.232955          0.931818   
merging_index_2layer               0.471212      0.420455          0.986364   
merging_index_3layer               0.340152      0.418182          0.963636   
Direct Query Engine                0.302273      0.097727          0.977273   

                           latency  total_cost  
app_id                                          
sentence window engine 1  6.000000    0.001837  
sentence window engine 3  7.659091    0.003286  
merging_index_2layer      6.000000    0.004402  
merging_index_3layer      6.000000    0.001687  
Direct Query Engine       6.000000    0.003478

# gradio

In [56]:
def format_chat_prompt(message, chat_history):
    prompt = ""
    for turn in chat_history:
        user_message, bot_message = turn
        prompt = f"{prompt}\nUser: {user_message}\nAssistant: {bot_message}"
    prompt = f"{prompt}\nUser: {message}\nAssistant:"
    return prompt

def respond(message, chat_history):
        formatted_prompt = format_chat_prompt(message, chat_history)
        bot_message = str(sentence_window_engine_1.query(formatted_prompt)) # using the best score
        chat_history.append((message, bot_message))
        return "", chat_history

In [ ]:
with gr.Blocks() as demo:
    chatbot = gr.Chatbot(height=240) #just to fit the notebook
    title = "עוזר באזרחות"
    theme="soft"
    msg = gr.Textbox(label="Prompt")
    btn = gr.Button("Submit")
    clear = gr.ClearButton(components=[msg, chatbot], value="Clear console")

    btn.click(respond, inputs=[msg, chatbot], outputs=[msg, chatbot])
    msg.submit(respond, inputs=[msg, chatbot], outputs=[msg, chatbot]) #Press enter to submit

gr.close_all()
demo.launch()